# Dependencies

In [22]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import folium
import os 
import geopy.distance
import geopandas
import math
from IPython.display import display

# Loading Data

In [23]:
# DATA

# parking=pd.read_csv("data/e-scooter_parks.csv")
parking=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\E-Scooter_Parks\\e-scooter_parks_point.csv")
view=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\E-Scooter OD\\wdl_od_view.csv")
metro_stops=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\GTFS\\gtfs_metro\\google_transit_dez2021\\stops.txt")
bus_stops=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\GTFS\\gtfs_bus\\stops.txt")
metro_stops=metro_stops[["stop_id","stop_name","stop_lat","stop_lon"]]
loc_center = [metro_stops['stop_lat'].mean(), metro_stops['stop_lon'].mean()]  ## mandatory to initialize the map

stops=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\GTFS\\gtfs_metro\\google_transit_dez2021\\stops.txt")
stop_times=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\GTFS\\gtfs_metro\\google_transit_dez2021\\stop_times.txt")

trips=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\Soft-Mobility\\Soft-Mobility\\GTFS\\gtfs_bus\\trips.txt")
taxi=pd.read_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\taxi_pickup.csv")

In [24]:
merged = pd.merge(stops, stop_times, on=['stop_id'])
data=list(zip(list(merged.groupby(['stop_id']).size()),list(pd.unique(merged['stop_id']))))
df = pd.DataFrame(data, columns = ['Total_trips', 'stop_id'])
df.set_index("stop_id", inplace = True)
stops = pd.merge(stops, df, on=['stop_id'])

# Maping all mobility points in Porto

In [54]:
## PORTO MAP
map1 = folium.Map(location = loc_center, tiles='Openstreetmap', zoom_start = 12, control_scale=True)


## PORTO METRO STATIONS ## BLUE POINTS
for index, loc in metro_stops.iterrows():
    folium.Marker([loc['stop_lat'], loc['stop_lon']],color="blue"  , radius=2, weight=5, popup=loc['stop_name']).add_to(map1)
folium.LayerControl().add_to(map1)


## PORTO E_SCOOTER STATIONS ## RED POINTS
for index, loc in parking.iterrows():
    folium.CircleMarker([loc['y'], loc['x']], popup=loc['toponimo'],color="red",  radius=2, weight=7).add_to(map1)
folium.LayerControl().add_to(map1)



## PORTO BUS STATIONS ## BLACK POINTS
for index, loc in bus_stops.iterrows():
    folium.CircleMarker([loc['stop_lat'], loc['stop_lon']],radius=1, weight=3, popup=loc['stop_name'],color="black",fill=False).add_to(map1)
folium.LayerControl().add_to(map1)

for index, loc in taxi.iterrows():
    folium.CircleMarker([loc['lat'], loc['long']],color="yellow"  , radius=5, weight=3).add_to(map1)
folium.LayerControl().add_to(map1)

display(map1)

In this map you can see all mobility points we have considered for this project. 
- The big blue markers are metro stations. 
- Black dots are bus stations. 
- Red dots are the E-scooter parkings spots as they are currently located.
- Yellow cirlces are "hotspots", based on taxi pick-ups data

You can use this map interactively to move around Porto and explore the current ditribution of the different forms of mobility.

# Feature extraction and data processing

In [26]:
#Create geopandas objects
metro_stop = geopandas.GeoDataFrame(metro_stops,geometry=geopandas.points_from_xy(metro_stops.stop_lon,metro_stops.stop_lat))
bus_stops = geopandas.GeoDataFrame(bus_stops,geometry=geopandas.points_from_xy(bus_stops.stop_lon,bus_stops.stop_lat))


# Providing a type name to each dataframe
metro_stops['type'] = 'metro'
parking['type'] = 'parking'
bus_stops['type'] = 'bus'

# Naming convention
parking['stop_name'] = parking['toponimo']
parking['stop_lat'] = parking['y'] 
parking['stop_lon'] = parking['x'] 

# Concatinating all datasets
df1 = metro_stops[['type','stop_name','stop_lat','stop_lon','geometry']]
df2 = bus_stops[['type','stop_name','stop_lat','stop_lon','geometry']]
df3 = parking[['type','stop_name','stop_lat','stop_lon','geometry']]


# Dataset concatinated row-wise
data = pd.concat([df1, df2, df3])

Calculate minimum distances between each scooter parking spot and metro station

In [27]:
mindist=list()
min_dist=100
min_metro_lat=float()
min_metro_lon=float()
min_parking_lat=float()
min_parking_lon=float()

for i,j in zip(data[data['type']=='parking']['stop_lat'],data[data['type']=='parking']['stop_lon']):
    min_dist=100
    my_list=list()
    min_metro_lat=float()
    min_metro_lon=float()
    min_parking_lat=float()
    min_parking_lon=float()
    
    for a,b in zip(data[data['type']=='metro']['stop_lat'],data[data['type']=='metro']['stop_lon']):    
        if geopy.distance.geodesic((i,j), (a,b)).km<min_dist:
            min_dist=geopy.distance.geodesic((i,j), (a,b)).km            
            min_metro_lat=a
            min_metro_lon=b
            min_parking_lat=i
            min_parking_lon=j
            
    my_list=[min_metro_lat, min_metro_lon, min_parking_lat, min_parking_lon, min_dist]
    mindist.append(my_list)

In [28]:
ParkingMetro = pd.DataFrame(mindist, columns = ['metro_lat', 'metro_lon', 'parking_lat', 'parking_lon', 'min_dist'])

Find all scooter parking spots that are within walking distance of a metro station

In [55]:
Min_Parking_Metro=ParkingMetro[ParkingMetro['min_dist']<0.34]

In [30]:
Min_Parking_Metro.rename({"metro_lat": "lat", 
                          "metro_lon": "long"}, 
                           axis = "columns", inplace = True)

C:\Users\emile\anaconda3\lib\site-packages\pandas\core\frame.py:4441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


Transforming data

In [31]:
Min_Parking_Metro['lat'] = pd.to_numeric(Min_Parking_Metro['lat']).round(2)
Min_Parking_Metro['long'] = pd.to_numeric(Min_Parking_Metro['long']).round(2)


<ipython-input-31-aaa5aa943e56>:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  Min_Parking_Metro['lat'] = pd.to_numeric(Min_Parking_Metro['lat']).round(2)
<ipython-input-31-aaa5aa943e56>:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  Min_Parking_Metro['long'] = pd.to_numeric(Min_Parking_Metro['long']).round(2)


In [32]:
taxi1 = taxi.copy(deep=True)

In [33]:
taxi['ind'] = list(range(163))
taxi1['ind'] = list(range(163))

Round of taxi pick-up coordinates to find hotspots

In [34]:
taxi['lat'] = pd.to_numeric(taxi['lat']).round(2)
taxi['long'] = pd.to_numeric(taxi['long']).round(2)

In [35]:
df = pd.merge(taxi, Min_Parking_Metro, how='outer', indicator=True, on=['lat', 'long'])
df=df.loc[df._merge == 'left_only',['lat', 'long','ind']]

In [36]:
df = pd.merge(taxi1, df, how='inner', on=['ind'])

In [56]:
# df=df[['lat_x','long_x']]
df=df.iloc[:, [0, 1]]
df.rename({"lat_x": "lat", 
                          "long_x": "long"}, 
                           axis = "columns", inplace = True)


In [39]:
df.to_csv("C:\\Users\\emile\\OneDrive\\Documents\\Masterstudier\\ISEG\\WDL\\stage_2\\taxi_hotspots.csv")

In [40]:
parking_leftover=pd.merge(parking, Min_Parking_Metro, left_on=  ['stop_lat', 'stop_lon'],
                   right_on= ['parking_lat', 'parking_lon'], 
                   how = 'outer', indicator=True)
parking_leftover=parking_leftover.loc[parking_leftover._merge == 'left_only',['stop_lat', 'stop_lon']]


In [57]:
hotspot=df

Calculate minimum distances between each scooter parking spot and hotspot

In [42]:
mindist=list()
min_dist=100
min_hotspot_lat=float()
min_hotspot_lon=float()
min_parking_lat=float()
min_parking_lon=float()

for i,j in zip(pd.to_numeric(parking_leftover['stop_lat']),pd.to_numeric(parking_leftover['stop_lon'])):
    min_dist=100
    my_list=list()
    min_hotspot_lat=float()
    min_hotspot_lon=float()
    min_parking_lat=float()
    min_parking_lon=float()
    
    for a,b in zip(pd.to_numeric(hotspot['lat']),pd.to_numeric(hotspot['long'])):    
        if geopy.distance.geodesic((i,j), (a,b)).km<min_dist:
            min_dist=geopy.distance.geodesic((i,j), (a,b)).km            
            min_hotspot_lat=a
            min_hotspot_lon=b
            min_parking_lat=i
            min_parking_lon=j
            
    my_list=[ min_parking_lat, min_parking_lon,min_hotspot_lat,min_hotspot_lon, min_dist]
    mindist.append(my_list)

In [43]:
ParkingHotspot = pd.DataFrame(mindist, columns = [ 'parking_lat', 'parking_lon','hotspot_lat', 'hotspot_lon', 'min_dist'])

In [60]:
# These are the hotspots that we can consider scooter parking with less than 0.34km away from them so we don't need to change those parkings
Min_Parking_Hotspot=ParkingHotspot[ParkingHotspot['min_dist']<0.34]

In [63]:
parking_leftover=pd.merge(parking_leftover, Min_Parking_Hotspot, left_on=  ['stop_lat', 'stop_lon'],
                   right_on= ['parking_lat', 'parking_lon'], 
                   how = 'outer', indicator=True)
parking_leftover=parking_leftover.loc[parking_leftover._merge == 'left_only',['stop_lat', 'stop_lon']]


Calculate distance between bus stops and the hotspots.
We do this to find if a hotspot is served by a bus stop within 100 meters.

In [47]:
mindist=list()
min_dist=100
min_BusStop_lat=float()
min_BusStop_lon=float()
min_taxi_lat=float()
min_taxi_lon=float()

for i,j in zip(pd.to_numeric(taxi['lat']),pd.to_numeric(taxi['long'])):
    min_dist=100
    my_list=list()
    min_BusStop_lat=float()
    min_BusStop_lon=float()
    min_taxi_lat=float()
    min_taxi_lon=float()
    
    for a,b in zip(pd.to_numeric(bus_stops['stop_lat']),pd.to_numeric(bus_stops['stop_lon'])):    
        if geopy.distance.geodesic((i,j), (a,b)).km<min_dist:
            min_dist=geopy.distance.geodesic((i,j), (a,b)).km            
            min_BusStop_lat=a
            min_BusStop_lon=b
            min_taxi_lat=i
            min_taxi_lon=j
            
    my_list=[ min_taxi_lat, min_taxi_lon,min_BusStop_lat,min_BusStop_lon, min_dist]
    mindist.append(my_list)
# mindist

In [48]:
HotspotBusstop = pd.DataFrame(mindist, columns = [ 'min_taxi_lat', 'min_taxi_lon','min_BusStop_lat', 'min_BusStop_lon', 'min_dist'])

Find all hotspots that do not have a bus station within 100 meters of them

In [49]:
# HotspotBusstop[HotspotBusstop['min_dist']>0.1].info()
scooter_bus=HotspotBusstop[HotspotBusstop['min_dist']>0.1]
scooter_bus.rename({"min_taxi_lat": "lat", 
                          "min_taxi_lon": "lon"}, 
                           axis = "columns", inplace = True)

C:\Users\emile\anaconda3\lib\site-packages\pandas\core\frame.py:4441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  return super().rename(


In [50]:
scooter_bus=scooter_bus.iloc[:,:2]

# Updated map

In [53]:
## PORTO MAP
map2 = folium.Map(location = loc_center, tiles='Openstreetmap', zoom_start = 12, control_scale=True)

#The most popular metro stations, larger metro stations have more number of stops
stops=stops[stops['Total_trips']>326.144578]
for index, loc in stops.iterrows():
    folium.CircleMarker([loc['stop_lat'], loc['stop_lon']], color="blue", radius= (math.sqrt(loc['Total_trips'] )/3), popup=(loc['stop_name'], loc['Total_trips'])).add_to(map2)

## PORTO Drop-off Zones that have to be relocated ## RED POINTS
for index, loc in parking_leftover.iterrows():
    folium.CircleMarker([loc['stop_lat'], loc['stop_lon']],color="red"  , radius=6, weight=7).add_to(map2)
folium.LayerControl().add_to(map2)

## PORTO E_SCOOTER STATIONS ## green POINTS
for index, loc in parking.iterrows():
    folium.CircleMarker([loc['stop_lat'], loc['stop_lon']], popup=loc['toponimo'],color="green",  radius=5, weight=5).add_to(map2)
folium.LayerControl().add_to(map2)



## Min_Parking_Hotspot hotspots that we can consider scooter parking with less than 0.34km

for index, loc in Min_Parking_Hotspot.iterrows():
    folium.CircleMarker([loc['parking_lat'], loc['parking_lon']],color="green",  radius=3, weight=3).add_to(map2)
folium.LayerControl().add_to(map2)


for index, loc in Min_Parking_Hotspot.iterrows():
    folium.CircleMarker([loc['hotspot_lat'], loc['hotspot_lon']],color="yellow"  , radius=5, weight=5).add_to(map2)
folium.LayerControl().add_to(map2)

for index, loc in scooter_bus.iterrows():
    folium.CircleMarker([loc['lat'], loc['lon']],color="gray"  , radius=2, weight=2).add_to(map2)
folium.LayerControl().add_to(map2)




display(map2)

In this map we can see the updated points of mobility
- The blue circles are the most popular metro stations in Porto, with larger circles indicating a larger number of daily stops at that station. If you press on a station you will see the station name, and the number of daily stops.
- The yellow markers are the hotspots of the city, which are well served by scooter parking spots.
- The purely green markers are the scooter parking spots which are within walking distance from a hotspot or a metro station. We believe that these are well located and should not be relocated.
- Finally, the green markers with red edges are the scooter parking spots that are outside of walking distance from either a hotspot or a metro station. We belive that these are not well located and they should be relocated.

Use this map intercatively to see which scooter parking spots should be re-evaluated. If you press on a parking spot you will see it's current adress.


# Spots that are not ideally located

In [65]:
parking_leftover

stop_lat  stop_lon
0   41.149252 -8.630972
1   41.147554 -8.667407
2   41.150085 -8.662277
3   41.153808 -8.613081
4   41.155044 -8.612300
..        ...       ...
66  41.163312 -8.586327
67  41.177352 -8.590054
68  41.170204 -8.657355
69  41.173360 -8.637309
70  41.167479 -8.659702

[71 rows x 2 columns]

This list, "parking_leftover" is the list of scooter parking spots that should be relocated. They are outside the walking distance of both any metro station and any hotspot.